In [1]:
import sys
sys.path.insert(1, '..')
from bokeh.io import show, output_notebook
from bokeh.layouts import column,row
output_notebook(hide_banner=True)
from cocoa import covid19 as co
from cocoa import display as cd
from cocoa import world as cw
import pandas as pd
w=cw.WorldInfo()

In [2]:
import importlib
importlib.reload(co)
importlib.reload(cd)
spf = co.DataBase('spf')
coco = cd.CocoDisplay()

SPF aka Sante Publique France database selected ...
... tree differents db from SPF will be parsed ...
fill_cocoa_field started
Available keys words for  spf  are :  ['hosp', 'rea', 'rad', 'dc', 'incid_hosp', 'incid_rea', 'incid_dc', 'incid_rad', 'P', 'T', 'tx_incid', 'R', 'taux_occupation_sae', 'tx_pos']
Last date data  11/5/20


In [3]:
import geopandas as gpd
import numpy as np
import pandas as pd

shapefile='https://datanova.laposte.fr/explore/dataset/geoflar-departements-2015/download/?format=shp&timezone=Europe/Berlin&lang=fr'
    
gdf = gpd.read_file(shapefile)[['code_dept','nom_dept','geometry','code_reg','nom_reg']]
gdf.sort_values("code_reg",inplace=True)
#gdf[["code_reg","nom_reg"]].groupby("code_reg").sum()

gdf2=gdf.copy()
list_translation={"GUADELOUPE":(63,23),
                  "MARTINIQUE":(63,23),
                  "GUYANE":(50,35),
                  "REUNION":(-51,60),
                  "MAYOTTE":(-38,51.5)}
for d,t in list_translation.items():
    gdf2.loc[gdf2["nom_dept"]==d,"geometry"]=gdf2[gdf2["nom_dept"]==d]["geometry"].translate(t[0],t[1])
gdf2.reset_index()

idf_translation=(-6.5,-5)
idf_scale=5
idf_center=(-4,44)
z=gdf2[gdf2["code_dept"].isin(['75','92','93','94'])].copy()
z['geometry']=z.translate(idf_translation[0],idf_translation[1]).scale(xfact=idf_scale,yfact=idf_scale,origin=idf_center)
z['code_reg']=0
z['nom_reg']='IDF PETITE COURONNE'
gdf2=gdf2.append(z)

gdf2 # used for maps only 

gdf_reg=gdf2.dissolve(by=['code_reg','nom_reg'], aggfunc='sum')[["geometry"]] # maps for regions

In [4]:
gdf["nom_reg"].unique()

array(['GUADELOUPE', 'MARTINIQUE', 'GUYANE', 'REUNION', 'MAYOTTE',
       'ILE-DE-FRANCE', 'CENTRE-VAL DE LOIRE', 'BOURGOGNE-FRANCHE-COMTE',
       'NORMANDIE', 'NORD-PAS-DE-CALAIS-PICARDIE',
       'ALSACE-CHAMPAGNE-ARDENNE-LORRAINE', 'PAYS DE LA LOIRE',
       'BRETAGNE', 'AQUITAINE-LIMOUSIN-POITOU-CHARENTES',
       'LANGUEDOC-ROUSSILLON-MIDI-PYRENEES', 'AUVERGNE-RHONE-ALPES',
       "PROVENCE-ALPES-COTE D'AZUR", 'CORSE'], dtype=object)

In [5]:
gdf["code_reg"].unique()

array(['01', '02', '03', '04', '06', '11', '24', '27', '28', '32', '44',
       '52', '53', '75', '76', '84', '93', '94'], dtype=object)

In [6]:
#first_dep_of_reg=[gdf[gdf["code_reg"]==r]["code_dept"].iloc[0] for r in gdf["code_reg"].unique() if int(r) > 10 ] # on prend 1 dep par région, on supprime l'outremer
first_dep_of_reg=[gdf[gdf["code_reg"]==r]["code_dept"].iloc[0] for r in gdf["code_reg"].unique() ] # on prend 1 dep par région, en gardant outremer

sp_reg=spf.get_stats(which='taux_occupation_sae',location=first_dep_of_reg) # récuperation des données

sp_reg['location']=[gdf[gdf['code_dept']==l]['nom_reg'].iloc[0] for l in sp_reg['location']] # on remplace département en nom de la région

show(coco.cocoa_basic_plot(sp_reg,'taux_occupation_sae'),plot_height=1000) # plot

In [7]:
latest_data=sp_reg[sp_reg["date"]==max(sp_reg["date"])]

In [8]:
merged=gdf_reg.merge(latest_data, left_on = 'nom_reg', right_on = 'location', how = 'right')[['geometry','location','taux_occupation_sae']]
geojson=merged.to_json()

In [12]:
from bokeh.io import curdoc, output_notebook, show
from bokeh.models import Slider, HoverTool, GeoJSONDataSource, LinearColorMapper, ColorBar
from bokeh.layouts import widgetbox, row, column
from bokeh.palettes import brewer
from bokeh.plotting import figure
from bokeh.palettes import brewer

#Input GeoJSON source that contains features for plotting.
geosource = GeoJSONDataSource( geojson=geojson )

#Define a sequential multi-hue color palette.
palette = brewer['Reds'][9]
palette = palette[::-1]

#Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors. Input nan_color.
color_mapper = LinearColorMapper(palette = palette, low = 0, high = 150, nan_color = '#d9d9d9')

#Add hover tool
hover = HoverTool(tooltips = [ ('Région','@location'),
                              ('Taux occupation','@taux_occupation_sae')])

#Create color bar. 
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8,width = 500, height = 20,
                     border_line_color=None,location = (0,0), orientation = 'horizontal')#, major_label_overrides = tick_labels)


#Create figure object.
p = figure(title = 'Taux occupation lits en réa', plot_height = 800 , plot_width = 580, tools = [hover]) # toolbar_location = None,
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

#Add patch renderer to figure. 
p.patches('xs','ys', source = geosource,fill_color = {'field' :'taux_occupation_sae', 'transform' : color_mapper}, line_color = 'black', line_width = 0.25, fill_alpha = 1)
p.add_layout(color_bar, 'below')

# Make a column layout of widgetbox(slider) and plot, and add it to the current document
layout = column(p)#,widgetbox(slider))
#curdoc().add_root(layout)

#Display plot inline in Jupyter notebook
output_notebook()

#Display plot
show(layout)

Loading BokehJS ...